In [1]:
# takes 60s per 40 api calls.
# download player tournament history. skip if already downloaded. player_id list is from BridgePowerRatings.

# previous steps:
# none

# next steps:
# create sql db of player tournament data.

# todo:
# Improve the method of issuing api calls only when needed. Write update info to file?
# Identify the correct player_id from list for each elite player name. Issue is that multiple players can have same name.

In [2]:
import pandas as pd
import pathlib
from collections import defaultdict
import mlBridgeLib

In [3]:
# override pandas display options
mlBridgeLib.pd_options_display()

In [4]:
rootPath = pathlib.Path('e:/bridge/data')
acblPath = rootPath.joinpath('acbl')
acblPath.mkdir(parents=True,exist_ok=True)
bprPath = rootPath.joinpath('bpr')
bprPath.mkdir(parents=True,exist_ok=True)

In [5]:
# takes 60s per 40 api calls.
# call acbl api to retrieve player's tournament data.
# todo: inexplicable variance between 'total' in json and sessions_count. Why? varaince is 0 to -15-ish.
import requests
import urllib
import time
import json
def download_tournaments(df,bearer_file):
    headers = {'accept':'application/json', 'Authorization':bearer[len('Authorization: '):]}
    start_time = time.time()
    get_count = 0
    for n,r in df.iterrows():
        player_ids = r['player_id']
        assert type(player_ids) is list, [type(player_ids), player_ids]
        #print(f"{time.strftime('%X')} player_id list:{player_ids} Name:{r['Name']} Rank:{r['Rank']}")
        print(f"{time.strftime('%X')} Name:{r['Name']} player_id list:{player_ids}")
        for player_id in player_ids:
            if player_id.startswith('tmp:') or player_id.startswith('#'): # somehow #139 crept into player_id
                print(f'Skipping player_id:{player_id}')
                continue
            else:
                print(f'Processing player_id:{player_id}')
            dirPath = acblPath.joinpath('players/'+player_id+'/tournaments')
            if dirPath.exists():
                session_file_count = len(list(dirPath.glob('*.session.json')))
                print(f'dir exists: file count:{session_file_count} dir:{dirPath}')
                if session_file_count > 0: # todo: temp?
                    print(f'dir not empty -- skipping')
                    continue
            else:
                print(f'Creating dir:{dirPath}')
                dirPath.mkdir(parents=True,exist_ok=True)
                session_file_count = 0
            path = 'https://api.acbl.org/v1/tournament/player/history_query'
            query = {'acbl_number':player_id,'page':1,'page_size':50,'start_date':'1900-01-01'}
            params = urllib.parse.urlencode(query)
            url = path+'?'+params
            sessions_count = 0
            while url:
                get_count += 1
                print(f"{n}/{len(df)} gets:{get_count} rate:{round((time.time()-start_time)/get_count,2)} url:{url}")
                #time.sleep(1) # throttle api calling. Maybe not needed as api is taking longer than 1s.
                response = requests.get(url, headers=headers)
                if response.status_code in [500]: # 500 is unknown response code. try skipping player
                    print(f'500: count:{get_count} skipping') # 4476921 - Thx Merle.
                    next_page_url = None
                    break
                assert response.status_code == 200, (n, url, response.status_code)
                json_response = response.json()
                json_pretty = json.dumps(json_response, indent=4)
                #print(json_pretty)
                next_page_url = json_response['next_page_url']
                sessions_total = json_response['total'] # is same for every page
                if sessions_total == session_file_count: # sometimes won't agree because identical sessions. older scores?
                    print(f'File count correct: {dirPath}: terminating {player_id} early.')
                    next_page_url = None
                    sessions_count = sessions_total
                    break
                for data in json_response['data']:
                    sessions_count += 1 # todo: oops, starts first one at 2. need to move
                    session_id = data['session_id']
                    filePath = dirPath.joinpath(session_id+'.session.json')
                    if filePath.exists():
                        print(f'{sessions_count}/{sessions_total}: File exists: {filePath}: skipping')
                        continue
                    print(f'{sessions_count}/{sessions_total}: Writing:',filePath)
                    with open(filePath,'w',encoding='UTF8') as f:
                        f.write(json.dumps(data, indent=4))
                url = next_page_url
            if sessions_count != sessions_total:
                print(f'Session count mismatch: {dirPath}: variance:{sessions_count-sessions_total}')

In [6]:
# read file containing api bearer secret. acbl calls it a "Personal Access Token". Available at https://api.acbl.org/
bearer_file = pathlib.Path('c:/sw/bridge/BridgePowerRatings/acbl_api_authorization_bearer_secret.txt')
with open(bearer_file,'rb') as f:
    bearer = f.read()

In [ ]:
# read all files downloaded from BridgePowerRatings. For each elite player name, download their tournament history.
# todo: rewrite to pass unique list of player_ids, names. 
files = bprPath.glob('*.pkl')
for f in files:
    df = pd.read_pickle(bprPath.joinpath(f))
    display(f'Processing file:{f} len:{len(df)}',df.head())
    if 'player_id' in df:
        assert 'Name' in df
        # todo: sort df (e.g. Rank) to better track progress of downloads?
        #df = df['Rank'].astype('float32').sort_values()
        download_tournaments(df,bearer_file)
print(f'Done: Total files processed:{len(files)}')

'Processing file:e:\\bridge\\data\\bpr\\allmps.pkl'

0 Rank      MP's Unit              Name  player_id
0    1  92862.58  128  Meckstroth, Jeff  [4580699]
1    2  87910.58  176     Passell, Mike  [1622382]
2    3  78168.46  128     Rodwell, Eric  [5482658]
3    4  76525.13  174       Wold, Eddie  [3443949]
4    5  71817.34  210        Lair, Mark  [5830400]

17:03:45 Name:Meckstroth, Jeff player_id list:['4580699']
Processing player_id:4580699
dir exists: file count:674 dir:e:\bridge\data\acbl\players\4580699\tournaments
dir not empty -- skipping
17:03:45 Name:Passell, Mike player_id list:['1622382']
Processing player_id:1622382
dir exists: file count:724 dir:e:\bridge\data\acbl\players\1622382\tournaments
dir not empty -- skipping
17:03:45 Name:Rodwell, Eric player_id list:['5482658']
Processing player_id:5482658
dir exists: file count:660 dir:e:\bridge\data\acbl\players\5482658\tournaments
dir not empty -- skipping
17:03:45 Name:Wold, Eddie player_id list:['3443949']
Processing player_id:3443949
dir exists: file count:787 dir:e:\bridge\data\acbl\players\3443949\tournaments
dir not empty -- skipping
17:03:45 Name:Lair, Mark player_id list:['5830400']
Processing player_id:5830400
dir exists: file count:732 dir:e:\bridge\data\acbl\players\5830400\tournaments
dir not empty -- skipping
17:03:45 Name:Itabashi, Mark player_id list:['6811434']
P

File count correct: e:\bridge\data\acbl\players\3530000\tournaments: terminating 3530000 early.
17:03:50 Name:Stansby, Lew player_id list:['8914737']
Processing player_id:8914737
dir exists: file count:285 dir:e:\bridge\data\acbl\players\8914737\tournaments
dir not empty -- skipping
17:03:50 Name:Onstott, John player_id list:['9593322']
Processing player_id:9593322
dir exists: file count:495 dir:e:\bridge\data\acbl\players\9593322\tournaments
dir not empty -- skipping
17:03:50 Name:DeMartino, Richard player_id list:['1182730']
Processing player_id:1182730
dir exists: file count:646 dir:e:\bridge\data\acbl\players\1182730\tournaments
dir not empty -- skipping
17:03:50 Name:Morse, Dan player_id list:['5573122']
Processing player_id:5573122
dir exists: file count:469 dir:e:\bridge\data\acbl\players\5573122\tournaments
dir not empty -- skipping
17:03:50 Name:Mohan, John player_id list:['4761685']
Processing player_id:4761685
dir exists: file count:737 dir:e:\bridge\data\acbl\players\476168

File count correct: e:\bridge\data\acbl\players\9503943\tournaments: terminating 9503943 early.
Processing player_id:6133126
dir exists: file count:445 dir:e:\bridge\data\acbl\players\6133126\tournaments
dir not empty -- skipping
Processing player_id:8983933
dir exists: file count:4 dir:e:\bridge\data\acbl\players\8983933\tournaments
dir not empty -- skipping
Processing player_id:6039758
dir exists: file count:132 dir:e:\bridge\data\acbl\players\6039758\tournaments
dir not empty -- skipping
Skipping player_id:tmp:2e16a3aa-29a3-4773-ad8a-66c686ff4cb7
Skipping player_id:tmp:ff92aaf1-f746-4f5f-8c34-496a6bb6e90e
17:03:53 Name:Wolpert, Gavin player_id list:['8149887']
Processing player_id:8149887
dir exists: file count:367 dir:e:\bridge\data\acbl\players\8149887\tournaments
dir not empty -- skipping
17:03:53 Name:Morris, Robert player_id list:['4057163', '5512883', '8888639']
Processing player_id:4057163
dir exists: file count:953 dir:e:\bridge\data\acbl\players\4057163\tournaments
dir not 

...

151/200: Writing: e:\bridge\data\acbl\players\8149631\tournaments\1805119-0601-2.session.json
152/200: Writing: e:\bridge\data\acbl\players\8149631\tournaments\1805119-041P-1.session.json
153/200: Writing: e:\bridge\data\acbl\players\8149631\tournaments\1805119-041T-1.session.json
154/200: Writing: e:\bridge\data\acbl\players\8149631\tournaments\1804046-071P-1.session.json
155/200: Writing: e:\bridge\data\acbl\players\8149631\tournaments\1801081-2703-1.session.json
156/200: Writing: e:\bridge\data\acbl\players\8149631\tournaments\1711103-022P-1.session.json
157/200: Writing: e:\bridge\data\acbl\players\8149631\tournaments\1711103-022T-1.session.json
158/200: Writing: e:\bridge\data\acbl\players\8149631\tournaments\1711103-0401-2.session.json
159/200: Writing: e:\bridge\data\acbl\players\8149631\tournaments\1711103-0401-1.session.json
160/200: Writing: e:\bridge\data\acbl\players\8149631\tournaments\1711103-021P-1.session.json
161/200: Writing: e:\bridge\data\acbl\players\8149631\tourna

51/88: Writing: e:\bridge\data\acbl\players\7352964\tournaments\1707079-151T-1.session.json
52/88: Writing: e:\bridge\data\acbl\players\7352964\tournaments\1707079-142P-1.session.json
53/88: Writing: e:\bridge\data\acbl\players\7352964\tournaments\1707079-142T-1.session.json
54/88: Writing: e:\bridge\data\acbl\players\7352964\tournaments\1706094-091P-1.session.json
55/88: Writing: e:\bridge\data\acbl\players\7352964\tournaments\1706094-091T-1.session.json
56/88: Writing: e:\bridge\data\acbl\players\7352964\tournaments\1611043-0601-2.session.json
57/88: Writing: e:\bridge\data\acbl\players\7352964\tournaments\1611043-0503-2.session.json
58/88: Writing: e:\bridge\data\acbl\players\7352964\tournaments\1607065-1001-2.session.json
59/88: Writing: e:\bridge\data\acbl\players\7352964\tournaments\1607065-091P-1.session.json
60/88: Writing: e:\bridge\data\acbl\players\7352964\tournaments\1607065-092P-1.session.json
61/88: Writing: e:\bridge\data\acbl\players\7352964\tournaments\1607065-0901-1.s

51/130: Writing: e:\bridge\data\acbl\players\7407858\tournaments\1703063-0401-1.session.json
52/130: Writing: e:\bridge\data\acbl\players\7407858\tournaments\1703063-0303-1.session.json
53/130: Writing: e:\bridge\data\acbl\players\7407858\tournaments\1703063-0301-1.session.json
54/130: Writing: e:\bridge\data\acbl\players\7407858\tournaments\1610107-151P-1.session.json
55/130: Writing: e:\bridge\data\acbl\players\7407858\tournaments\1610107-151T-1.session.json
56/130: Writing: e:\bridge\data\acbl\players\7407858\tournaments\1610107-141P-1.session.json
57/130: Writing: e:\bridge\data\acbl\players\7407858\tournaments\1610107-141T-1.session.json
58/130: Writing: e:\bridge\data\acbl\players\7407858\tournaments\1609098-05O1-1.session.json
59/130: Writing: e:\bridge\data\acbl\players\7407858\tournaments\1609098-03O1-1.session.json
60/130: Writing: e:\bridge\data\acbl\players\7407858\tournaments\1609098-02O1-1.session.json
61/130: Writing: e:\bridge\data\acbl\players\7407858\tournaments\16070

51/89: Writing: e:\bridge\data\acbl\players\2057239\tournaments\1707002-SS02-3.session.json
52/89: Writing: e:\bridge\data\acbl\players\2057239\tournaments\1707002-SS02-1.session.json
53/89: Writing: e:\bridge\data\acbl\players\2057239\tournaments\1707002-SS01-1.session.json
54/89: Writing: e:\bridge\data\acbl\players\2057239\tournaments\1704010-01P2-1.session.json
55/89: Writing: e:\bridge\data\acbl\players\2057239\tournaments\1704010-01T1-1.session.json
56/89: Writing: e:\bridge\data\acbl\players\2057239\tournaments\1704010-31P2-1.session.json
57/89: Writing: e:\bridge\data\acbl\players\2057239\tournaments\1704010-31P1-1.session.json
58/89: Writing: e:\bridge\data\acbl\players\2057239\tournaments\1701002-07P2-1.session.json
59/89: Writing: e:\bridge\data\acbl\players\2057239\tournaments\1701002-07P1-1.session.json
60/89: Writing: e:\bridge\data\acbl\players\2057239\tournaments\1701002-06P3-1.session.json
61/89: Writing: e:\bridge\data\acbl\players\2057239\tournaments\1701002-06P2-1.s

51/117: Writing: e:\bridge\data\acbl\players\7937822\tournaments\1611003-121T-1.session.json
52/117: Writing: e:\bridge\data\acbl\players\7937822\tournaments\1611003-122P-1.session.json
53/117: Writing: e:\bridge\data\acbl\players\7937822\tournaments\1611003-122T-1.session.json
54/117: Writing: e:\bridge\data\acbl\players\7937822\tournaments\1610002-151T-1.session.json
55/117: Writing: e:\bridge\data\acbl\players\7937822\tournaments\1610002-151P-1.session.json
56/117: Writing: e:\bridge\data\acbl\players\7937822\tournaments\1610002-1501-1.session.json
57/117: Writing: e:\bridge\data\acbl\players\7937822\tournaments\1610002-142T-1.session.json
58/117: Writing: e:\bridge\data\acbl\players\7937822\tournaments\1610002-142P-1.session.json
59/117: Writing: e:\bridge\data\acbl\players\7937822\tournaments\1610002-141T-1.session.json
60/117: Writing: e:\bridge\data\acbl\players\7937822\tournaments\1610002-141P-1.session.json
61/117: Writing: e:\bridge\data\acbl\players\7937822\tournaments\16080